## Debugging msprime role sims
Simplifying all the role simulation code to focus on getting to the msprime stuff to debug behavior.
To understand the nuts and bolts of the role/msprime interface, see the role-msprime-dev.ipynb

In [101]:
%load_ext rpy2.ipython
%load_ext autoreload
%autoreload 2

import msprime
import newick
import numpy as np
import pandas as pd

from role_msprime import _force_ultrametric, py_msprime_simulate

from collections import Counter, defaultdict
from IPython.display import display


The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython
The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Parameterize and run a role simulation

In [102]:
%%R -o model -o J_m -o J -o curtime -o metaTree -o metaAbund -o localAbund -o localTDiv -o alpha -o sequence_length -o mu
library(roleR)
library(ape)

targetStep = 3

newick <- function(phylo){
     ape_tree <- as(phylo, "phylo")
     write.tree(ape_tree, file = 'temp.nwk', append = FALSE, digits = 40, tree.names = FALSE)
     nwk <- readChar('temp.nwk', file.info('temp.nwk')$size)
     #unlink('temp.nwk')
     nwk
}

p <- roleParams(individuals_local = 1000, individuals_meta = 10000,
                         species_meta = 10, speciation_local = 0, 
                         speciation_meta = 0.05, extinction_meta = 0.05, env_sigma = 0.5,
                         trait_sigma=1,comp_sigma = 0.5, dispersal_prob = 0.01, mutation_rate = 1e-7,
                         equilib_escape = 1, num_basepairs = 500, alpha = 10000,
                         init_type = 'oceanic_island', niter = 1e6, niterTimestep = 1e5)
model <- runRole(roleModel(p))

## the timesteps at which data were recorded
## TODO: Doing it this way because the as() above is broken atm
iterations <- c(0, which(1:model@params@niter %% model@params@niterTimestep == 0))

## Global parameters
J_m <- model@params@individuals_meta
mu <- model@params@mutation_rate
sequence_length <- model@params@num_basepairs

## For each snapshot
for (idx in 1:length(model@modelSteps)){
    idx = 10

    ## Fetch the data that we need to run the msprime simulation
    ## Current time in timesteps (necessary to get divergence counting from t_0)
    ## TODO: If as(model, "roleExperiment") works then you can do this instead.
    #curtime = exp@experimentMeta$iterations[[idx]]
    curtime = iterations[[idx]]

    ## Prior to iterFun it was done this way:
    ##J <- model@params@individuals_local[[idx]]
    J <- model@params@individuals_local(idx)
    alpha <- model@params@alpha(idx)

    metaTree <- newick(model@modelSteps[[idx]]@phylo)
    metaAbund <- model@modelSteps[[idx]]@metaComm@spAbund

    localAbund <- model@modelSteps[[idx]]@localComm@indSpecies
    localTDiv <- model@modelSteps[[idx]]@localComm@spLastOriginStep

    ## Returns a dataframe with rows for pi, TajD and genotypes
    #res <- py_msprime_simulate(J_m, J, curtime, metaTree, metaAbund, localAbund, localTDiv, alpha, sequence_length, mu)

    ## Update the model with the results
    #model@modelSteps[[idx]]@localComm@spGenDiv = unlist(res["pi",])
    #model@modelSteps[[idx]]@localComm@indSeqs = unlist(res["gtypes",])
}

In [124]:
res_df, demography, ts = py_msprime_simulate(J_m[0], J[0], curtime[0], metaTree[0], metaAbund,
                    localAbund, localTDiv, alpha[0], sequence_length[0], mu[0],
                    seed=12345, verbose=True, return_debug=True)
res_df


    J_m  - 10000
    J - 1000.0
    curtime - 900000.0
    metaTree - ((((t3:5.269056710998022197145473910495638847351,t5:5.269056710998022197145473910495638847351):8.073028464703590145745693007484078407288,t1:13.34208517570161234289116691797971725464):42.34082106974287995626582414843142032623,t10:55.68290624544449229915699106641113758087):42.24208307215433677583860117010772228241,((t2:4.460709240081939697120105847716331481934,t9:4.460709240081939697120105847716331481934):76.85817990162274782051099464297294616699,(t8:19.11984274225734736774029443040490150452,(t4:10.29205610798750569756521144881844520569,(t6:1.150299163493230025778757408261299133301,t7:1.150299163493230025778757408261299133301):9.141756944494275671786454040557146072388):8.827786634269841670175082981586456298828):62.19904639944734014989080606028437614441):16.60610017589414155736449174582958221436);

    metaAbund - [6.90545501e-01 1.93899506e-01 7.03708391e-02 2.73383116e-02
 1.07581319e-02 4.30325275e-03 1.77192760e-03

t1   
pi                                                 0.0008  \
TajD                                            -0.816497   
gtypes  [TCCGGAGGTCCCGCCACTGTTATACGTCTGATAGTTCCTGGTCTT...   

                                                       t2   
pi                                                 0.0016  \
TajD                                            -0.972558   
gtypes  [CCAAGAACAAACGTGTGCAGCCACTAATCCCGTTTTGACCGGAGA...   

                                                       t3  
pi                                                 0.0008  
TajD                                            -0.816497  
gtypes  [TGATCCGTCGGCCATGCGTTCACATGCACATGTCGGCAGTGGGTC...

## Get the rest of the necessary data

In [104]:
## Plot the tree and mutations
## With large trees/lots of mutations this can be SLOW!
wide_fmt = (1200, 250)
# Create a stylesheet that shrinks labels and rotates leaf labels, to avoid overlap
node_label_style = (
    ".node > .lab {font-size: 80%}"
    ".leaf > .lab {text-anchor: start; transform: rotate(90deg) translate(6px)}"
)
nd_labels = {}  # An array of labels for the nodes
for n in ts.nodes():
    # Set sample node labels from metadata. Here we use the population name, but you might want
    # to use the *individual* name instead, if the individuals in your tree sequence have names
    if n.is_sample():
        nd_labels[n.id] = ts.population(n.population).metadata["name"]

ts.first().draw_svg(
    size=wide_fmt,
    time_scale="log_time",
    y_gridlines=True,
    y_axis=True,
    y_ticks=[100, 1000, 10000],
    node_labels=nd_labels,
    mutation_labels=defaultdict(lambda:''),
    style=node_label_style,
)


## Fetch pi, tajD, & genotype data for each sampled population

In [120]:
## Get a dictionary mapping population ids to the list of node IDs per population
nodeIDs = defaultdict(lambda: [])
for n in ts.nodes():
    if n.is_sample():
        nodeIDs[ts.population(n.population).metadata["name"]].append(n.id)

nodeIDs

defaultdict(<function __main__.<lambda>()>,
            {'t1_l': [0, 1, 2, 3, 4],
             't2_l': [5, 6, 7, 8, 9],
             't3_l': [10, 11, 12, 13, 14],
             't6_l': [15, 16, 17, 18, 19]})

In [126]:
res = {}
for popname, idxs in nodeIDs.items():
    print(popname, idxs)
    ## Split off the _l so the pop name agrees with the name in local_df
    pname = popname.split("_")[0]
    res[pname] = []
    res[pname].append(ts.diversity(sample_sets=idxs))
    res[pname].append(ts.Tajimas_D(sample_sets=idxs))
#    res[pname].append(ts.genotype_matrix(samples=idxs).T)
    res[pname].append(list(ts.haplotypes(samples=idxs)))
res_df = pd.DataFrame(res, index=["pi", "TajD", "gtypes"])
pd.concat([local_df, res_df])
res_df

t1_l [0, 1, 2, 3, 4]
t2_l [5, 6, 7, 8, 9]
t3_l [10, 11, 12, 13, 14]
t6_l [15, 16, 17, 18, 19]


t1   
pi                                                    0.0  \
TajD                                                  NaN   
gtypes  [ATAGGTCAATAGTATTGCCGAACACGCCGAGTAACACCGCGCAGG...   

                                                       t2   
pi                                                 0.0056  \
TajD                                            -0.174749   
gtypes  [ATAGGACTTATATGTGTAGGAGAGACTATGAGTTAGTACTCCGAC...   

                                                       t3   
pi                                                    0.0  \
TajD                                                  NaN   
gtypes  [GGCGCACGACTCGGTTGCGCCACGTCCCTGTGCATGATGCATGGG...   

                                                       t6  
pi                                                 0.0024  
TajD                                             1.224745  
gtypes  [TACCCACGAGGAGCGTATGAAGCCGCACATCAAAACGAAATCTTA...

In [124]:
list(ts.haplotypes(samples=[0, 1, 2, 3, 4]))

['ATAGGTCAATAGTATTGCCGAACACGCCGAGTAACACCGCGCAGGACGCTCTAAGCACCTGATAGTCCGCTATGACACTTCACCGCGAAAGAGCAATTTCCGCCGGGGTCCTCAGTAGGGTACACATCCCCCTGACCACTTAAAAGAAAGATGATATGACTACATCTCAAAGACACCAGGGTAGTTTCAATAAATGCTAAATAGATCGCGTGGCTGGGTTCTAGGCCCTAGCACTAATCAAAGTCTCTCT',
 'ATAGGTCAATAGTATTGCCGAACACGCCGAGTAACACCGCGCAGGACGCTCTAAGCACCTGATAGTCCGCTATGACACTTCACCGCGAAAGAGCAATTTCCGCCGGGGTCCTCAGTAGGGTACACATCCCCCTGACCACTTAAAAGAAAGATGATATGACTACATCTCAAAGACACCAGGGTAGTTTCAATAAATGCTAAATAGATCGCGTGGCTGGGTTCTAGGCCCTAGCACTAATCAAAGTCTCTCT',
 'ATAGGTCAATAGTATTGCCGAACACGCCGAGTAACACCGCGCAGGACGCTCTAAGCACCTGATAGTCCGCTATGACACTTCACCGCGAAAGAGCAATTTCCGCCGGGGTCCTCAGTAGGGTACACATCCCCCTGACCACTTAAAAGAAAGATGATATGACTACATCTCAAAGACACCAGGGTAGTTTCAATAAATGCTAAATAGATCGCGTGGCTGGGTTCTAGGCCCTAGCACTAATCAAAGTCTCTCT',
 'ATAGGTCAATAGTATTGCCGAACACGCCGAGTAACACCGCGCAGGACGCTCTAAGCACCTGATAGTCCGCTATGACACTTCACCGCGAAAGAGCAATTTCCGCCGGGGTCCTCAGTAGGGTACACATCCCCCTGACCACTTAAAAGAAAGATGATATGACTACATCTCAAAGACACCAGGGTAGTTTCAATAAATGCTAAATAGATCGCGTGGCTGGGTTCTAGGCCCTAGCA

# Trash below here

## Debugging newick trees

In [256]:
#msprime.species_trees.parse_newick(nwk[0], 10**6)
def parse_newick(tree, branch_length_multiplier):
    """
    Parses the newick tree and annotates the resulting nodes with their
    time values, appropriately scaled.
    """
    # Parse the newick tree string.
    parsed = newick.loads(tree)
    if len(parsed) == 0:
        raise ValueError(f"Not a valid newick tree: '{tree}'")
    root = parsed[0]

    # Set node depths (distances from root).
    stack = [(root, 0)]
    num_nodes = 0
    max_depth = 0
    while len(stack) > 0:
        node, depth = stack.pop()
        if depth > max_depth:
            max_depth = depth
        num_nodes += 1
        node.depth = depth
        for child in node.descendants:
            stack.append((child, depth + child.length))
    if num_nodes < 3:
        raise ValueError("Newick tree must have at least three nodes")

    # Set node times (distances from present).
    for node in root.walk():
        node.time = (max_depth - node.depth) * branch_length_multiplier
        print(node.name, node.is_leaf, node.time)
        # We don't allow non ultrametric trees for now because it's unclear
        # how we should deal with taking samples in this case. The code
        # all works perfectly well other than this, though.
        if node.is_leaf:
            if abs(node.time) > 1e-8:  # Arbitrary cutoff
                raise ValueError(
                    f"All leaf populations must be at time 0: time={node.time}"
                )
        print(node.name, node.is_leaf, node.time)
    return root
#t = parse_newick(nwk[0], 10**6)
print()
#for node in t.walk():
#    print(node, node.time, node.length, node._length)

wat = "(((((t6:2.45112382300675335500272922218,t8:2.45112382300675335500272922218):9.79658819007364911612967262045,t3:12.2477120130804024711324018426):0.274339041983090226040076231584,t4:12.5220510550634926971724780742):18.933448771541357302794494899,t10:31.4554998266048499999669729732):121.547048353778492923993326258,(((t5:1.18211007899886055838578613475,t1:1.18211007899886055838578613475):2.39764699703194139601691858843,(t7:0.98689255753362914447279763408,t2:0.98689255753362914447279763408):2.5928645184971728099299070891):16.3437354032475887777309253579,t9:19.9234924792783907321336300811):133.07905570110494863911299035);"
print(wat)
wat = _force_ultrametric(wat)
print(wat)
t = parse_newick(wat, 10**6)
print(wat)
t.newick


(((((t6:2.45112382300675335500272922218,t8:2.45112382300675335500272922218):9.79658819007364911612967262045,t3:12.2477120130804024711324018426):0.274339041983090226040076231584,t4:12.5220510550634926971724780742):18.933448771541357302794494899,t10:31.4554998266048499999669729732):121.547048353778492923993326258,(((t5:1.18211007899886055838578613475,t1:1.18211007899886055838578613475):2.39764699703194139601691858843,(t7:0.98689255753362914447279763408,t2:0.98689255753362914447279763408):2.5928645184971728099299070891):16.3437354032475887777309253579,t9:19.9234924792783907321336300811):133.07905570110494863911299035);
None 0.0
None 121.5470483537785
None 18.933448771541357
None 0.2743390419830902
None 9.79658819007365
t6 2.4511238230067534
t8 2.4511238230067534
t3 12.247712013080402
t4 12.522051055063521
t10 31.45549982660488
None 133.07905570110495
None 16.34373540324759
None 2.3976469970319414
t5 1.1821100789989174
t1 1.1821100789989174
None 2.592864518497173
t7 0.9868925575336576
t2 

'(((((t6:2.4511238230067534,t8:2.4511238230067534):9.79658819007364911612967262045,t3:12.247712013080402):0.274339041983090226040076231584,t4:12.522051055063521):18.933448771541357302794494899,t10:31.45549982660488):121.547048353778492923993326258,(((t5:1.1821100789989174,t1:1.1821100789989174):2.39764699703194139601691858843,(t7:0.9868925575336576,t2:0.9868925575336576):2.5928645184971728099299070891):16.3437354032475887777309253579,t9:19.92349247927842):133.07905570110494863911299035)'

In [198]:
import toytree
print(t.newick)
print(nwk[0])
#ntree = toytree.tree(nwk[0], tree_format=0)
_ = ntree.draw()

(((t8:23.23024077574185142225360323209315538406,t5:23.23024077574185142225360323209315538406):24.26146708828785492073620844166725873947,((t2:8.072970319062299893175804754719138145447,t7:8.072970319062299893175804754719138145447):19.73836336416463055343228916171938180923,t3:27.81133368322693044660809391643851995468):19.68037418080277589638171775732189416885):22.48603930835695052792289061471819877625,((t1:7.183044919322398413896735291928052902222,t10:7.183044919322398413896735291928052902222):4.833259304519728516424947883933782577515,(t9:4.754958914543507830785529222339391708374,(t6:2.768425059009238964335963828489184379578,t4:2.768425059009238964335963828489184379578):1.986533855534268866449565393850207328796):7.261345309298619099536153953522443771362):57.96144294854452994059101911261677742004)
(((t8:23.23024077574185142225360323209315538406,t5:23.23024077574185142225360323209315538406):24.26146708828785492073620844166725873947,((t2:8.072970319062299893175804754719138145447,t7:8.0729703

<svg class="toyplot-canvas-Canvas" xmlns:toyplot="http://www.sandia.gov/toyplot" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns="http://www.w3.org/2000/svg" width="265.0px" height="275.0px" viewBox="0 0 265.0 275.0" preserveAspectRatio="xMidYMid meet" style="background-color:transparent;border-color:#292724;border-style:none;border-width:1.0;fill:rgb(16.1%,15.3%,14.1%);fill-opacity:1.0;font-family:Helvetica;font-size:12px;opacity:1.0;stroke:rgb(16.1%,15.3%,14.1%);stroke-opacity:1.0;stroke-width:1.0" id="t6315f325905e47e38676cacfe36a72a2"> t9 t5 t8 t6 t1 t2 t10 t3 t4 t7

In [255]:
def _force_ultrametric(tree):
    """
    Force all leaf nodes to time 0
    Input a newick tree in string format
    Output is a modified newick tree with all leafs having equal total length
    """
    # Parse the newick tree string.
    parsed = newick.loads(tree)
    if len(parsed) == 0:
        raise ValueError(f"Not a valid newick tree: '{tree}'")
    root = parsed[0]

    # Set node depths (distances from root).
    stack = [(root, 0)]
    max_depth = 0
    while len(stack) > 0:
        node, depth = stack.pop()
        if depth > max_depth:
            max_depth = depth
        node.depth = depth
        for child in node.descendants:
            stack.append((child, depth + child.length))
    for node in root.walk():
        if node.is_leaf:
            ## Add offset to node.length to foce all nodes to fall at time 0
            node.length = node.length + (max_depth - node.depth)
        print(node.name, node.length)
    return root.newick
wat = "(((((t6:2.45112382300675335500272922218,t8:2.45112382300675335500272922218):9.79658819007364911612967262045,t3:12.2477120130804024711324018426):0.274339041983090226040076231584,t4:12.5220510550634926971724780742):18.933448771541357302794494899,t10:31.4554998266048499999669729732):121.547048353778492923993326258,(((t5:1.18211007899886055838578613475,t1:1.18211007899886055838578613475):2.39764699703194139601691858843,(t7:0.98689255753362914447279763408,t2:0.98689255753362914447279763408):2.5928645184971728099299070891):16.3437354032475887777309253579,t9:19.9234924792783907321336300811):133.07905570110494863911299035);"
_force_ultrametric(wat)

None 0.0
None 121.5470483537785
None 18.933448771541357
None 0.2743390419830902
None 9.79658819007365
t6 2.4511238230067534
t8 2.4511238230067534
t3 12.247712013080402
t4 12.522051055063521
t10 31.45549982660488
None 133.07905570110495
None 16.34373540324759
None 2.3976469970319414
t5 1.1821100789989174
t1 1.1821100789989174
None 2.592864518497173
t7 0.9868925575336576
t2 0.9868925575336576
t9 19.92349247927842


'(((((t6:2.4511238230067534,t8:2.4511238230067534):9.79658819007364911612967262045,t3:12.247712013080402):0.274339041983090226040076231584,t4:12.522051055063521):18.933448771541357302794494899,t10:31.45549982660488):121.547048353778492923993326258,(((t5:1.1821100789989174,t1:1.1821100789989174):2.39764699703194139601691858843,(t7:0.9868925575336576,t2:0.9868925575336576):2.5928645184971728099299070891):16.3437354032475887777309253579,t9:19.92349247927842):133.07905570110494863911299035)'

In [27]:
import newick
print(newick.__version__)
print(nwk[0])
tree = newick.loads(nwk[0])[0]
print(tree.ascii_art())

1.7.0
(((((t1:12.81909994,(t8:4.50543671,t7:4.50543671):8.313663226):4.664673682,(t9:7.510527151,t3:7.510527151):9.973246468):26.24487534,(t5:14.08435921,t6:14.08435921):29.64428975):13.09992292,t2:56.82857188):20.44951288,(t10:21.04719718,t4:21.04719718):56.23088758);

                              ┌─t1
                        ┌─────┤
                        │     │     ┌─t8
                        │     └─────┤
                  ┌─────┤           └─t7
                  │     │     ┌─t9
            ┌─────┤     └─────┤
            │     │           └─t3
      ┌─────┤     │     ┌─t5
      │     │     └─────┤
      │     │           └─t6
──────┤     │
      │     └─t2
      │     ┌─t10
      └─────┤
            └─t4


In [205]:
ts_tmp = msprime.sim_ancestry(
    samples=[msprime.SampleSet(num_samples=5, population="t3_l", time=1000, ploidy=1),
            msprime.SampleSet(num_samples=5, population="t3_l", time=0, ploidy=1)],
            demography=demography,
            sequence_length=250,
            ploidy=1,
            random_seed=2)
ts_tmp = msprime.sim_mutations(ts_tmp, rate=mu*1)
ts_tmp.genotype_matrix().T

array([[0, 0, 1],
       [0, 0, 1],
       [0, 0, 1],
       [0, 0, 1],
       [1, 0, 0],
       [1, 0, 0],
       [0, 0, 1],
       [0, 0, 1],
       [0, 1, 0],
       [0, 0, 0]], dtype=int32)

## Trash

In [117]:
#s = pd.DataFrame([1,3,5,6], index=local_df.columns, columns=["pi"])
#pd.concat([local_df, s.T], axis=0)
res_df = pd.DataFrame(res, index=["pi", "TajD", "gtypes"])
pd.concat([local_df, res_df])

t1   
local_abund                                               68.0  \
meta_abund                                         6905.455006   
tdiv                                                      20.0   
pi                                                         0.0   
TajD                                                       0.0   
pi                                                         0.0   
TajD                                                       NaN   
gtypes       [[1, 3, 3, 3, 3, 1, 2, 1, 3, 3, 0, 0, 3, 2, 0,...   

                                                            t2   
local_abund                                               19.0  \
meta_abund                                         1938.995064   
tdiv                                                     18.16   
pi                                                         0.0   
TajD                                                       0.0   
pi                                                      0.0056   
TajD                                                 -0.174749   
gtypes       [[1, 3, 3, 3, 3, 3, 2, 3, 0, 2, 3, 2, 3, 1, 0,...   

                                                            t3   
local_abund                                                5.0  \
meta_abund                                          703.708391   
tdiv                                                     18.72   
pi                                                         0.0   
TajD                                                       0.0   
pi                                                         0.0   
TajD                                                       NaN   
gtypes       [[0, 0, 0, 3, 0, 3, 2, 0, 3, 0, 3, 1, 1, 1, 0,...   

                                                            t6  
local_abund                                                8.0  
meta_abund                                           43.032528  
tdiv                                                      9.26  
pi                                                         0.0  
TajD                                                       0.0  
pi                                                      0.0024  
TajD                                                  1.224745  
gtypes       [[2, 1, 0, 1, 0, 3, 2, 0, 3, 1, 2, 2, 1, 0, 1,...